# TP 3: Smoothed Particle Hydrodynamics (SPH)

**Université Paris-Saclay, M1 MFL, MNMF**

Nom, Prénom = ...

#### 🔥🔥🔥 Consignes 🔥🔥🔥

Rédiger votre compte rendu directement dans ce notebook Jupyter. Toute forme de collaboration est **fortement encouragée**, mais **le copié-collé ne sera pas toléré**. Le compte rendu sera à déposer sur eCampus.

La méthode SPH enseignée en cours permet de simuler un écoulement faiblement compressible en non-visqueux et à surface libre. Il s'agit d'une méthode Lagrangienne, dans laquelle on suit la densité, la position et la vitesse d'un grand nombre de ''particules'' de fluide. 

Des explosions aux vagues géantes déferlantes aux trainées de bateaux, la méthode SPH a été intégrée dans la plupart de logiciels permettant de créer ces animations. Parmi les différents utilisateurs de cette méthode, on compte aussi l'industrie de l'animation pour jeux vidéo et effets spéciaux. 

La première partie du TP est essentiellement dédiée au schéma d'interpolation SPH. Dans la deuxième partie, on donnera un exemple d'un code qui permet de simuler l'écoulement de ''sloshing'' dans un réservoir 2D. 

## 1. Interpolation SPH d'une fonction
### 1.1 Théorie  

On note $\vec{x}$ le vecteur qui décrit la position dans un domaine $\Omega$. Pour toute fonction $f(\vec{x})$ on peut écrire que

$$
f(\vec{x} ) = \int_\Omega f(\vec{x}' ) \,  \delta (\vec{x} - \vec{x}') \, dV' 
$$

Dans la méthode SPH, on remplace la distribution de Dirac $\delta (\vec{x} - \vec{x}')$ par un noyau plus lisse $W (\vec{x} - \vec{x}', h )$ qui tend vers la distribution de Dirac dans la limite $h\rightarrow 0$. On obtient alors 

$$
f(\vec{x} )  \approx  \int_\Omega f(\vec{x}' ) \,  W (\vec{x} - \vec{x}', h ) \, dV' 
$$

Si on discrétise ensuite l'intégrale par une formule de quadrature simple qui intègre sur des sous-domaines $\Omega_j$ de $\Omega$ aux barycentres $\vec{x}_j$, on obtient finalement

$$
 f(\vec{x} )    \approx  \langle f(\vec{x} ) \rangle^h = \sum_{j=0}^{N_p-1} f (\vec{x}_j)  \ w_j  
 \,  W (\vec{x} - \vec{x}_j , h    )
$$

Ici $\vec{x}_j$ sont $N_p$ positions d'espace discrètes (les points de quadrature) et $w_j$ sont des poids d'intégration que l'on peut assimiler aux volumes des sous-domaines. On initialisera les particules sur un maillage uniforme à pas d'espace $\delta x$ selon chaque direction de l'espace. Dans ce cas, les poids d'intégration sont $w_j = \delta x^d$ par tout $j = 0, \ldots, N_p-1$ avec $d$ la dimension. 

Dans ce TP, on choisit le noyau $W$ comme un spline cubique = une fonction cubique par morceaux: 

$$
W (\vec{x}, h ) = C_c \left \{  \begin{array}{rcl} 
\dfrac{2}{3} - q^2 + \dfrac{q^3}{2} & , & 0 \leq q \leq 1 \\
\dfrac{1}{6} (2-q)^3 & , &  1 \leq q \leq 2 \\
\dfrac{}{}  0 & , & q \geq 2
\end{array} \right . \quad \mbox{avec} \quad q = \frac{|| \vec{x} || }{h}
$$

On appelle $h$ la longueur de lissage. Cette fonction satisfait 7 propriétés : elle a son maximum en $q=0$ et elle est continue et 2 fois continûment différentiable en $q=1$ et $q=2$. La constante de normalisation $C_c$ est telle que

$$
\int_{\Omega}  W (\vec{x},h) \,  d V = 1 \label{norma}
$$

ce qui donne  

$$
\mbox{1D:} \quad C_c = \frac{1}{h} \quad, \quad \mbox{2D:} \quad C_c = \frac{30}{14 \pi h^2}
$$

pour 1 et 2 dimensions. Dans ce qui suit, on réalisera quelques tests du schéma d'interpolation. 

### 1.2. Visualisation de la fonction $W(x,h)$

Dans la prochaine cellule, définir la fonction Wcal $W(x,h)$ en 1D. 

In [ ]:
import numpy as np

def Wcal(x,h):
    ...

Servez vous de la fonction pour afficher la fonction $W(x,h)$ sur l'intervalle $x \in [-3,3]$ et pour quelques valeurs de $h = 0.1,0.2,0.5,1$ différents (sur le même graphe) 

In [ ]:
import matplotlib.pyplot as plt

...

On constatera que plus que $h$ est petit, plus que la fonction est localisée autour en $x=0$. On imagine que  $W(x,h)$ tend bien vers une distribution de Dirac dans la limite $h\rightarrow 0$.  Vérifier que l'intégrale sous la courbe vaut bien 1. 

In [ ]:
from scipy import integrate
h=...
W_int=integrate.quadrature(Wcal, ...,...,args=(h),tol=1e-16,maxiter=1000)
print("L'aire sous la courbe vaut ",W_int)

De manière générale en python, il faut toujours tenter d'éviter les boucles si cela est possible car peut diminuer fortement la vitesse d'execution du code.  Dans la cellule suivante, on programme la même fonction Wcal, mais au lieu du test ```if ... elif  ```, on utilise un filtre logique. 

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from scipy import integrate

def Wcal(x,h):
    #calcul de la fonction d'interpolation W(x,h) en 2D
    q=np.abs(x)/h
    C=1./h

    W=C*((2./3-q**2+(q**3)/2)*(q<1)+(((2-q)**3)/6)*((q>1)*(q<2)))
    return W


### 1.3 Exemple d'interpolation : partition de l'unité

Dans cette section, on teste le schéma d'interpolation SPH sur la fonction constante $ f(x) = 1$. On parle de la partition de l'unité. Le but est de vérifier comment la fonction

$$
 \langle 1 \rangle^h (x)  = \sum_{j=0}^{N_p-1}  \ w_j  
 \,  W (x - x_j , h )  
$$

se rapproche de la fonction $f(x)=1$ et comment cela dépend des valeurs de $h$, du nombre de points $N_p$ et la distance $\delta x = w_j$ entre ces points. 

Pour fixer les idées, on choisit un intervalle $x\in[-3,3]$, que l'on imagine découpé en $N_p$ sous-intervalles de taille 

$$
\delta x = \frac{6}{N_p} 
$$

et on définit 

$$
x_j =-3 + \frac{\delta x }{2} + j \delta x    \ , \quad j=0,\ldots, N_p-1
$$

Ainsi, les points $x_j$ se trouvent aux centres des $N_p$ sous-intervalles.  

Dans la cellule suivante, on commence par fixer $N_p$ et le rapport 

$$
\alpha = \frac{h}{dx}
$$

qui sera un paramètre important pour la qualité de l'interpolation. Ensuite :

* On calcule $\delta x$ et $h$. 
* On construit un tableau ```xj_tab``` qui contient les positions des particules $x_j$. 
* On définit un maillage plus fin $x$ de 401 points entre $-3$ et $3$. 
* On affiche pour tout $j=0,\ldots,N_p-1$ les fonctions $w_j  \,  W (x - x_j , h )$ en couleur.
* Au fur et à mesure, on calcule la somme $\sum_{j=0}^{N_p-1} $ dans la variable ```unite``` que l'on affiche en noir à la fin. Ceci permet de voir graphiquement, comment l'unité a été décomposée par le schéma d'interpolation SPH. 

In [ ]:
#nombre de sous-intervalles et alpha=h/dx : varier ces paramètres un peu
Np=20
alpha=1

#calcul dx et h
dx=...
h=...

#calcul des positions xj et poids d'intégration
xj_tab=...
wj=...

#maillage fin
x=np.linspace(...)

#ouvrir une fenêtre de figure
fig=plt.figure(figsize=(8,4))

#on calcule l'interpolation de l'unite comme u_interp
un_interp=np.zeros(len(x))
for j in range(Np):
    ...    #calcul la fonction W (x-x_j,h) 
    ...   #on affiche graphiquement les différents termes W (x-x_j,h)*wj  dans la somme 
    ...   #incrémenter un_interp de W*wj

#afficher la fonction interpolée    
plt.plot(x,un_interp,'k')
plt.xlabel('x')
plt.ylabel('f(x) = 1 ? ')
plt.title('Partition de l\'unité')
plt.grid()
plt.show()


Utiliser le code de ci-dessus pour répondre à la question suivante.

**Question:** Varier manuellement le facteur $\alpha \in [0.5,2]$. Comment doit-on choisir $\alpha = h / \delta x$ pour une interpolation de qualité, $\alpha>1$ ou $\alpha<1$ ? Suggérer une valeur de $\alpha = h/\delta x$ convenable. 

...


### 1.3 Exemple d'interpolation : fonction à support compact

Dans cette section, on étudie la fonction à support compact

$$
f(x) = \left (1- 3 x+ 4x^2 -5 x^3 \right ) \, e^{-x^2}
$$

Support compact signifie que la fonction tend rapidement vers zéro en dehors d'un certain intervalle. Ici $e^{-x^2}$ garantit une décroissance rapide de la fonction pour $|x|$ grand. 
Le but de l'exercice qui suit est de tester le schéma d'interpolation sur cette fonction, c.a.d. est-ce que

$$
\langle f \rangle^h (x) = \sum_{j=0}^{N_p-1}  f(x_j) \ w_j  
 \,  W (x - x_j , h )  
$$

reproduit bien la fonction $f(x)$ ?  On choisit encore l'intervalle $x\in[-3,3]$, que l'on découpera en $N_p$ sous-intervalles de longueur $\delta x = 6/N_p$ et avec les points

$$
x_j =-3 + \frac{\delta x }{2} + j \delta x    \ , \quad j=0,\ldots, N_p-1
$$

comme avant. Dans la cellule suivante: 

* Définir la fonction Python ```fcomp``` qui représente la fonction $f(x)$. 

* Réutiliser le même maillage $x$ fin de la précédente section, puis calculer  ```f_exact``` comme la fonction $f(x)$ exacte sur ce maillage. 

* Utilisant la definition de ```Np, alpha, dx, h,xj_tab``` de l'exercice précédent, calculer à l'aide d'une boucle, $\langle f \rangle^h (x)$ dans la variable nommée ```f_interp```. 

* Afficher  la fonction exacte (noir) et la fonction interpollée (rouge pointillé) en même temps sur le même graphe. 

* Calculer et  afficher à l'écran l'écart maximal entre la fonction exacte et son interpolation sur ce maillage. 

In [ ]:
def fcomp(x):
    return ...

#maillage fin et fonction exacte
x=np.linspace(...)
f_exact=fcomp(x)


Np=80
alpha=1.4

dx=...
h=...

xj_tab=...
wj=...


#on calcule l'interpolation 
#de maniere iterative
f_interp=np.zeros(len(x))
for j in range(Np):
    ...

fig=plt.figure(figsize=(8,4))
plt.plot(x,f_exact,'k',label='exact')
plt.plot(x,f_interp,'r--',label='interp')
plt.xlabel('x')
plt.ylabel('f (x) ')
plt.title('Partition de l\'unité pour N_p = '+str(Np)+', h/dx = '+str(h/dx)+', dx = '+str(dx))
plt.legend()
plt.grid()
plt.show()

print('Erreur maximale: ',max(np.abs(f_exact-f_interp)))

Dans la cellule suivante, on fixera $h/dx = \alpha = 1.2$ fixe, puis on varie $N_p$ (et donc $\delta x$) afin d'étudier quantitativement comment l'erreur maximale varie en fonction de $dx$. Afficher l'erreur en fonction dx utiliser un diagramme loglog. Afin d'éviter des biais introduits par les phénomènes de bord, on teste la qualité de l'interpolation sur un maillage fin $x\in [-2,2]$ sur 401 points (l'interpolation en $x$ suffisamment loin de $x_0$ et $x_{N_p-1}$ ne sera plus sous l'influence des effets de bord.)   

In [ ]:
Np_list=np.array([10,20,50,100,200,500,1000,2000])
alpha=1.2

x=np.linspace(...)
f_exact=fcomp(x)

err_list=np.zeros(len(Np_list))
dx_list=np.zeros(len(Np_list))
for i,Np in enumerate(Np_list):

    dx=...
    h=...

    xj_tab=...
    wj=...


    #on calcule l'interpolation
    #de maniere iterative
    f_interp=np.zeros(len(x))
    for j in range(Np):
        ...

    err_list[i]=max(np.abs(f_exact-f_interp))
    dx_list[i]=dx
    
fig=plt.figure(figsize=(8,4))
plt.loglog(dx_list,err_list,'b+-')
plt.xlabel('dx')
plt.ylabel('erreur absolue')
plt.grid()
plt.show()

**Question:** Quel ordre de convergence $p$ est-ce vous trouvez ? 

...

**Question:**  L'erreur maximale ne tend pas toujours vers zéro dans la limite $\delta x \rightarrow 0$ et avec $h/\delta x \geq 1$? Est-ce qu'on observe la même chose avec la norme L2 ? 

$$
\epsilon_{L_2} = \sqrt{ \frac{1}{N} \sum_{j=0}^{N-1} || f(x_j) - \langle f\rangle^h (x_j) ||^2 }
$$

Ici $x_j$ sont les $N = 401$ points du maillage ```x```. 

...
 

## 2. Interpolation du gradient d'une fonction
### 2.1 Théorie

Soit $f(\vec{x})$ un champ scalaire dont on souhaite calculer le gradient $\vec{\nabla} f$ par une approximation SPH. On peut alors appliquer le principe de base de l'interpolation

$$
\vec{\nabla} f (\vec{x} ) = \int_\Omega \vec{\nabla}' f(\vec{x}' ) \,  \delta (\vec{x} - \vec{x}') \, dV'   \approx  \int_\Omega \vec{\nabla}' f(\vec{x}' ) \,  W (\vec{x} - \vec{x}', h ) \, dV' 
$$

Par une intégration par partie, on aboutit à 

$$
\begin{array}{rcl}
\vec{\nabla} f(\vec{x} ) & \approx & -    \int_\Omega  f(\vec{x}' ) \,  \vec{\nabla}' W (\vec{x} - \vec{x}', h ) \, dV'  + \underbrace{ \oint_{\delta \Omega}  f(\vec{x}' ) \,  W (\vec{x} - \vec{x}', h )  \, d \vec{S} }_{\approx \ \vec{0}, \ \mbox{ loin de la paroi}}
\end{array}
$$

L'intégrale de bord ne contribue pas tant que $\vec{x}$ reste à des distances $>2h$ de la paroi. Puis, avec $\vec{\nabla}' W (\vec{x}- \vec{x}', h ) = - \vec{\nabla} W (\vec{x}- \vec{x}', h )$, on trouve la formule plus simple

$$
\vec{\nabla} f(\vec{x} )
\approx   \int_\Omega  f(\vec{x}' ) \,  \vec{\nabla} W (\vec{x} - \vec{x}', h ) \, dV' 
$$

valable loin des bords. La discrétisation de cette intégrale par une formule de quadrature mène à

$$
\vec{\nabla}  f(\vec{x} )  \approx  \langle \vec{\nabla} f(\vec{x} ) \rangle^h =   \sum_{j=0}^{N_p-1}   f(\vec{x}_j ) \,  \vec{\nabla} W (\vec{x} - \vec{x}_j, h ) \, w_j 
$$



### 2.2 Visualisation de la fonction $\vec{\nabla} W $


On commence par définir la fonction du gradient. On rappelle que 

$$
W (\vec{x}, h ) = C_c \left \{  \begin{array}{rcl} 
\dfrac{2}{3} - q^2 + \dfrac{q^3}{2} & , & 0 \leq q \leq 1 \\
\dfrac{1}{6} (2-q)^3 & , &  1 \leq q \leq 2 \\
\dfrac{}{}  0 & , & q \geq 2
\end{array} \right . \quad \mbox{avec} \quad q = \frac{|| \vec{x} || }{h}
$$

Ainsi, nous avons 

$$
\vec{\nabla} W = \frac{\partial W}{\partial q} \,  \vec{\nabla} q
$$

La fonction $\frac{\partial W}{\partial q} $ est facile à évaluer. Le vecteur $\vec{\nabla} q$ est trouvé par calcul indiciel 

$$
\vec{\nabla} q = \vec{\nabla}  \left ( \frac{|| \vec{x} || }{h} \right ) = \vec{e}_j \, \frac{\partial}{\partial x_j } \left ( \frac{ \sqrt{x_i x_i } }{h} \right ) =    \frac{\vec{e}_j}{2h} \frac{1}{\sqrt{x_k x_k }} \frac{\partial }{\partial x_j} \left ( x_i  x_i \right ) = \frac{\vec{e}_j}{2h} \frac{1}{\sqrt{x_k x_k }} 2 \delta_{ij} x_i =  \frac{x_j\vec{e}_j}{h} \frac{1}{\sqrt{x_k x_k }}
$$ 

soit

$$
 \vec{\nabla} q = \frac{1}{h} \frac{\vec{x}}{|| \vec{x} ||}  = \frac{\vec{x}}{qh^2} 
$$

Ainsi on obtient $\vec{\nabla} W (\vec{x}, h) $ comme

$$
\vec{\nabla} W  (\vec{x}, h ) = \frac{C_c \, \vec{x} }{h^2}  \left \{  \begin{array}{rcl} 
 - 2  + \dfrac{3 q}{2} & , & 0 \leq q \leq 1 \\
-\dfrac{1}{2q} (2-q)^2 & , &  1 \leq q \leq 2 \\
\dfrac{}{}  0 & , & q \geq 2
\end{array} \right . \quad \mbox{avec} \quad q = \frac{|| \vec{x} || }{h}
$$

et $C_c = 1/h$ en 1D, $C_c = 30/(14 \pi h^2)$ en 2D comme avant. 

Dans la cellule suivante, définir puis visualiser la fonction gradient en 1D.  

In [ ]:
def gradWcal(x,h):
    ...
    return gradW



Ci dessous, on définit la fonction de manière matricielle ce qui peut être plus efficace dans des langages de programmation comme Python. 

In [ ]:
def gradWcal(x,h):
    
    #calcul de la fonction d'interpolation W(x,h) en 2D
    q=np.abs(x)/h
    Cc=1./h

    gradW=Cc*x/(h**2)*((-2+3*q/2)*(q<1)+((-(0.5/(q+0.001*(q==0)))*(2-q)**2))*((q>1)*(q<2)))

    return gradW

**Question:** Quel est l'intérêt de la notation ```((-(0.5/(q+0.001*(q==0)))*(2-q)**2))*((q>1)*(q<2)))``` dans la fonction de ci-dessus. Pourquoi y a-t-il  ```q+0.001*(q==0)``` et pas juste ```q```?

...

### 2.3 Exemple d'interpolation de gradient : fonction linéaire


Afin de tester l'interpolation du gradient, on vérifie qu'en calculant le gradient d'une fonction linéaire $f(x)=x$, on retrouve bien 

$$
1 \approx    \sum_{j=0}^{N_p-1} x  \ \partial_x W (x - x_j, h ) \, w_j 
$$

Dans la cellule suivante proposer un code numérique qui calcule l'approximation de zéro ```dundx_interp``` à l'aide de cette formule et qui visualise cette fonction ensemble avec les termes  $\partial_x W ({x} - {x}_j, h ) \, w_j$, un peu comme on la vu plus haut pour la partition de l'unité. 

In [ ]:
#nombre de sous-intervalles et alpha=h/dx : varier ces paramètres un peu
Np=20
alpha=1

#calcul dx et h
dx=...
h=...



### 2.4 Trouver une valeur adéquate de $h/\delta x$.

De l'exercice sur l'interpolation de  $f(x)=1$  et du gradient de la fonction $f(x)=x$ on déduit que les quantités  

$$
\epsilon_1 = | \sum_{j=0}^{N_p-1}   W (x - x_j, h ) \, w_j  -1 |
$$
et

$$
\epsilon_2 =  | \sum_{j=0}^{N_p-1} C  \ \partial_x W (x - x_j, h ) \, w_j - 1 |
$$

doivent tendre vers zéro pour avoir une bonne interpolation. Ici on étudie la convergence des deux mesures en même temps et pour $x$ fixe. On prendra $N_p=401$ points $x_i \in [-3,3]$.  

Pour $x=0$, varier le paramètre $\alpha = h/\delta x \in [0.5,3]$ et calculer les quantités $\epsilon_1 $ et $\epsilon_2$. Afficher graphiquement $\epsilon_1$ et $\epsilon_2$ en fonction de $\alpha$. Proposez une valeur adéquate pour $\alpha = h/\delta x$.

## 3. Sup: Interpolation SPH en 2D

Afin de vous familiariser avec le schéma d'interpolation SPH en 2D, vous pouvez ici tenter de faire quelques tests similaires mais en 2D. Pour cela, il faudra

* Definir les fonctions ```Wcal(x,y,h)``` et ```gradWcal(x,y,h)``` en 2D. Ces fonctions doivent être capable de recevoir des matrices ```x,y``` de coordonnées de points.

* Afficher ces fonctions sur un domaine rectangulaire à l'aide d'un code couleur ou comme une surface (pour $W(x,y,h)$) ou comme un champ vectoriel (pour $\vec{\nabla}W (x,y,h)$).  

* Tester la partition de l'unité en 2D

* Vérifier que le gradient d'une fonction constante vaut bien 0.



